<a href="https://colab.research.google.com/github/HenryLimaa/Jobs/blob/main/DesafioPP_AB1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Desafio de Programação: Classificação de Pistas de Pouso em Imagens de Satélite**

## **Abordagem: Utilizando Google Earth Engine**

In [66]:
# @title INSTALAÇÃO DE BIBLIOTECAS

!pip install earthengine-api geemap matplotlib -q
print("Bibliotecas instaladas!")

Bibliotecas instaladas!


In [67]:
# @title AUTENTICAÇÃO GOOGLE EARTH ENGINE

import ee
import geemap
import matplotlib.pyplot as plt

try:
    ee.Initialize()
    print("Google Earth Engine inicializado!")
except Exception as e:
    print("Autenticando no Earth Engine...")
    ee.Authenticate()
    ee.Initialize()

Google Earth Engine inicializado!


In [68]:
# @title CONFIGURAÇÃO COM 150KM DE RAIO

# Coordenadas precisas do Aeroporto de Altamira
altamira_airport = [-52.2540, -3.2530]

# Área de 150km de raio (área muito grande - 70,650 km²)
roi_150km = ee.Geometry.Point(altamira_airport).buffer(150000)  # 150km
roi_150km = ee.Geometry.Point(altamira_airport).buffer(100000)  # 100km
roi_50km = ee.Geometry.Point(altamira_airport).buffer(50000)    # 50km
roi_10km = ee.Geometry.Point(altamira_airport).buffer(10000)    # 10km
roi_5km = ee.Geometry.Point(altamira_airport).buffer(5000)      # 5km
roi_2km = ee.Geometry.Point(altamira_airport).buffer(2000)      # 2km para teste rápido

print("Aeroporto de Altamira:", altamira_airport)
print("Área de análise: 150km de raio")
print("Área total: {:,} km²".format(int(3.14 * 150 * 150)))
print("Abrange múltiplos municípios do Pará")

Aeroporto de Altamira: [-52.254, -3.253]
Área de análise: 150km de raio
Área total: 70,650 km²
Abrange múltiplos municípios do Pará


In [69]:
# @title FUNÇÃO OTIMIZADA PARA IMAGENS (150KM) COM NDVI

def get_sentinel2_with_ndvi(roi):
    """Obtém imagem Sentinel-2 com cálculo de NDVI"""
    print("Buscando imagem Sentinel-2 para área de 150km...")

    collection = (ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')
                 .filterBounds(roi)
                 .filterDate('2024-06-01', '2024-08-31')  # Estação seca
                 .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 15))
                 .sort('CLOUDY_PIXEL_PERCENTAGE')
                 .first())

    image = collection

    # Calcular NDVI
    ndvi = image.normalizedDifference(['B8', 'B4']).rename('NDVI')

    # Adicionar NDVI à imagem
    image_with_ndvi = image.addBands(ndvi)

    print("Imagem e NDVI calculados!")
    return image_with_ndvi

In [70]:
# @title VISUALIZAÇÃO DA ÁREA DE 150KM

def quick_area_preview():
    """Visualização da área de estudo de 150km"""
    print("\n VISUALIZAÇÃO DA ÁREA DE ESTUDO (150KM RAIO)")

    Map = geemap.Map(center=[-3.2530, -52.2540], zoom=8)

    # Adicionar áreas concêntricas
    Map.addLayer(roi_150km, {'color': 'red', 'fillColor': 'FF000010'}, 'Área 150km')
    Map.addLayer(roi_50km, {'color': 'orange', 'fillColor': 'FF800020'}, 'Área 50km')
    Map.addLayer(roi_10km, {'color': 'yellow', 'fillColor': 'FFFF0030'}, 'Área 10km')
    Map.addLayer(roi_5km, {'color': 'green', 'fillColor': '00FF0020'}, 'Área 5km')

    # Ponto do aeroporto
    airport_point = ee.Geometry.Point(altamira_airport)
    Map.addLayer(airport_point, {'color': 'purple', 'pointSize': 20}, 'Aeroporto Altamira')

    return Map

In [71]:
# @title MAPA INTERATIVO COMPLETO COM SENTINEL-2 RGB, NDVI E GOOGLE SATELLITE
def create_interactive_map_with_layers(image, roi):
    """Cria mapa interativo com layers Sentinel-2 RGB, NDVI e Google Satellite"""
    print("\n CRIANDO MAPA INTERATIVO COM LAYERS")

    Map = geemap.Map(center=[-3.2530, -52.2540], zoom=8)

    # LAYER 1: Google Satellite (Mapa de satélite do Google)
    print(" Adicionando layer Google Satellite...")
    Map.add_tile_layer(
        url='https://mt1.google.com/vt/lyrs=s&x={x}&y={y}&z={z}',
        name='Google Satellite',
        attribution='Google',
        shown=True  # Visível por padrão
    )

    # LAYER 2: Sentinel-2 RGB (Banda True Color)
    print(" Adicionando layer Sentinel-2 RGB...")
    rgb_params = {
        'bands': ['B4', 'B3', 'B2'],
        'min': 0,
        'max': 3000,
        'gamma': 1.3
    }
    Map.addLayer(image.clip(roi), rgb_params, 'Sentinel-2 RGB', False)  # False = oculto por padrão

    # LAYER 3: NDVI (Normalized Difference Vegetation Index)
    print(" Adicionando layer NDVI...")
    ndvi_params = {
        'min': -1,
        'max': 1,
        'palette': ['blue', 'white', 'green', 'darkgreen']
    }
    Map.addLayer(image.select('NDVI').clip(roi), ndvi_params, 'NDVI - Vegetação', False)

    # LAYER 4: Áreas de estudo
    Map.addLayer(roi_150km, {'color': 'red', 'fillColor': '00000000'}, 'Área 150km', True)
    Map.addLayer(roi_50km, {'color': 'orange', 'fillColor': '00000000'}, 'Área 50km', False)
    Map.addLayer(roi_10km, {'color': 'yellow', 'fillColor': '00000000'}, 'Área 10km', False)

    # LAYER 5: Aeroporto e cidades
    airport_point = ee.Geometry.Point(altamira_airport)
    Map.addLayer(airport_point, {'color': 'purple', 'pointSize': 15}, 'Aeroporto Altamira', True)

    # Adicionar pontos das cidades na região
    cities_150km = {
        'Altamira': [-52.2540, -3.2530],
        'Anapu': [-51.1833, -3.4667],
        'Vitória do Xingu': [-51.9833, -2.8833],
        'Brasil Novo': [-52.4833, -3.5333],
        'Uruará': [-53.7500, -3.7167]
    }

    for city, coords in cities_150km.items():
        point = ee.Geometry.Point(coords)
        Map.addLayer(point, {'color': 'blue', 'pointSize': 8}, f'{city}', False)

    # LAYER 6: Detecção de pistas
    try:
        rgb = image.select(['B4', 'B3', 'B2'])
        brightness = rgb.reduce(ee.Reducer.mean()).rename('brightness')
        runway_candidates = brightness.gt(2000)
        Map.addLayer(runway_candidates.clip(roi),
                    {'palette': ['000000', '00FF00'], 'opacity': 0.6},
                    'Áreas Claras (Pistas)', False)
    except:
        pass

    # LAYER 7: Detecção avançada (NDVI + Brilho)
    try:
        enhanced_mask = enhanced_runway_detection(image, roi)
        Map.addLayer(enhanced_mask.clip(roi),
                   {'palette': ['000000', 'FF0000'], 'opacity': 0.7},
                   'Detecção Avançada (NDVI + Brilho)', False)
    except:
        pass

    # Adicionar controle de layers
    Map.addLayerControl()

    print(" Mapa interativo criado com sucesso!")
    print(" Layers disponíveis:")
    print("   • Google Satellite (VISÍVEL)")
    print("   • Sentinel-2 RGB (OCULTO)")
    print("   • NDVI - Vegetação (OCULTO)")
    print("   • Áreas de estudo")
    print("   • Cidades da região")
    print("   • Detecção de áreas claras")
    print("   • Detecção avançada")

    return Map

In [72]:
# @title ATUALIZAR MENSAGEM DE INSTRUÇÕES
def update_instructions():
    """Atualiza as instruções para incluir o Google Satellite"""
    print("\n COMO USAR O MAPA:")
    print("   • Use o controle no canto superior direito para ligar/desligar layers")
    print("   • Google Satellite: Mapa de satélite de alta resolução")
    print("   • Sentinel-2 RGB: Imagem atual da região")
    print("   • NDVI: Mostra vegetação (verde = muita vegetação)")
    print("   • Detecção Avançada: Áreas vermelhas = possíveis pistas")
    print("   • Dica: Compare Google Satellite com Sentinel-2 para análise temporal")

In [73]:
# @title FUNÇÃO PARA ANÁLISE DE NDVI
def analyze_ndvi(image, roi):
    """Análise específica do NDVI na região"""
    print("\n ANÁLISE DO NDVI NA REGIÃO DE 150KM")

    try:
        # Estatísticas do NDVI
        ndvi_stats = image.select('NDVI').reduceRegion(
            reducer=ee.Reducer.mean().combine(
                reducer2=ee.Reducer.stdDev(),
                sharedInputs=True
            ),
            geometry=roi,
            scale=1000,  # Escala maior para performance
            maxPixels=1e8,
            bestEffort=True
        )

        ndvi_mean = ndvi_stats.get('NDVI_mean').getInfo()
        ndvi_std = ndvi_stats.get('NDVI_stdDev').getInfo()

        if ndvi_mean is not None:
            print(f" Estatísticas do NDVI:")
            print(f"   • Média: {ndvi_mean:.3f}")
            print(f"   • Desvio padrão: {ndvi_std:.3f}")

            # Interpretação do NDVI
            if ndvi_mean > 0.6:
                veg_status = "Muita vegetação (floresta densa)"
            elif ndvi_mean > 0.3:
                veg_status = "Vegetação moderada"
            elif ndvi_mean > 0.1:
                veg_status = "Pouca vegetação (áreas abertas)"
            else:
                veg_status = "Solo exposto/área urbana"

            print(f"   • Status: {veg_status}")

            return ndvi_mean, ndvi_std
        else:
            print(" Não foi possível calcular estatísticas do NDVI")
            return None, None

    except Exception as e:
        print(f" Erro na análise do NDVI: {e}")
        return None, None

In [74]:
# @title DETECÇÃO DE PISTAS COM SUPORTE A NDVI
def enhanced_runway_detection(image, roi):
    """Detecção melhorada usando NDVI para excluir vegetação"""
    print(" Executando detecção avançada...")

    image_roi = image.clip(roi)

    # 1. Usar NDVI para remover vegetação
    ndvi = image_roi.select('NDVI')
    non_vegetation = ndvi.lt(0.3)  # Áreas com pouca vegetação

    # 2. Calcular brilho das áreas não vegetadas
    rgb = image_roi.select(['B4', 'B3', 'B2'])
    brightness = rgb.reduce(ee.Reducer.mean()).rename('brightness')

    # 3. Combinar condições: pouca vegetação + alta reflectância
    bright_areas = brightness.gt(1800)
    runway_candidates = non_vegetation.And(bright_areas)

    # 4. Limpeza morfológica
    cleaned = runway_candidates.focal_max(20).focal_min(10)

    return cleaned.rename('enhanced_runways')

In [75]:
# @title EXECUÇÃO PRINCIPAL COM LAYERS COMPLETOS
def main_with_layers():
    """Execução principal com mapa interativo completo"""
    print("=== DETECÇÃO DE PISTAS - MAPA INTERATIVO COMPLETO ===")
    print(" Área de abrangência: 150km raio")
    print(" Layers: Sentinel-2 RGB + NDVI")
    print("="*60)

    try:
        # 1. Visualização inicial da área
        print("1.  Visualizando área de estudo...")
        area_map = quick_area_preview()
        display(area_map)

        # 2. Obter imagem com NDVI
        print("\n2.  Obtendo imagem Sentinel-2 com NDVI...")
        image_with_ndvi = get_sentinel2_with_ndvi(roi_150km)
        print(" Imagem processada com sucesso!")

        # 3. Análise do NDVI
        print("\n3.  Analisando vegetação na região...")
        ndvi_mean, ndvi_std = analyze_ndvi(image_with_ndvi, roi_150km)

        # 4. Criar mapa interativo completo
        print("\n4.  Criando mapa interativo com layers...")
        interactive_map = create_interactive_map_with_layers(image_with_ndvi, roi_150km)

        # 5. Detecção avançada
        print("\n5.  Executando detecção avançada...")
        enhanced_mask = enhanced_runway_detection(image_with_ndvi, roi_150km)

        # Adicionar layer de detecção avançada ao mapa
        interactive_map.addLayer(enhanced_mask.clip(roi_150km),
                               {'palette': ['000000', 'FF0000'], 'opacity': 0.7},
                               'Detecção Avançada (NDVI + Brilho)', False)

        print(" Camada de detecção avançada adicionada!")

        # 6. Exibir mapa final
        display(interactive_map)

        print("\n" + "="*60)
        print(" MAPA INTERATIVO COMPLETO CRIADO!")
        print("\n COMO USAR O MAPA:")
        print("   • Use o controle no canto superior direito para ligar/desligar layers")
        print("   • Sentinel-2 RGB: Visão natural da região")
        print("   • NDVI: Mostra vegetação (verde = muita vegetação)")
        print("   • Detecção Avançada: Áreas vermelhas = possíveis pistas")
        print("   • Zoom: Use scroll do mouse para aproximar")

        if ndvi_mean is not None:
            print(f"\n NDVI médio: {ndvi_mean:.3f} ({'alta' if ndvi_mean > 0.6 else 'média' if ndvi_mean > 0.3 else 'baixa'} vegetação)")

        return interactive_map, image_with_ndvi

    except Exception as e:
        print(f" Erro na execução: {e}")
        return None, None

In [76]:
# @title EXECUTAR CÓDIGO COMPLETO COM LAYERS
print(" INICIANDO ANÁLISE COMPLETA COM LAYERS")
print(" Layers incluídos: Sentinel-2 RGB + NDVI")
print(" Área: 150km raio ao redor de Altamira")
print("="*60)

try:
    # Executar análise principal
    final_map, final_image = main_with_layers()

    if final_map:
        print("\n ANÁLISE CONCLUÍDA COM SUCESSO!")
        print("\n DICAS DE INTERPRETAÇÃO:")
        print("   • Áreas VERDES no NDVI = Floresta densa")
        print("   • Áreas AZUIS/BRANCAS no NDVI = Solo exposto/urbano")
        print("   • Áreas VERMELHAS na detecção = Possíveis pistas")
        print("   • Compare os layers para melhor análise")

        # Informações adicionais
        print("\n AEROPORTOS NA REGIÃO:")
        print("   • Altamira (principal) - coordenadas: [-52.2540, -3.2530]")
        print("   • Procure por formas retangulares claras próximas a cidades")

except Exception as e:
    print(f" ERRO FINAL: {e}")

 INICIANDO ANÁLISE COMPLETA COM LAYERS
 Layers incluídos: Sentinel-2 RGB + NDVI
 Área: 150km raio ao redor de Altamira
=== DETECÇÃO DE PISTAS - MAPA INTERATIVO COMPLETO ===
 Área de abrangência: 150km raio
 Layers: Sentinel-2 RGB + NDVI
1.  Visualizando área de estudo...

 VISUALIZAÇÃO DA ÁREA DE ESTUDO (150KM RAIO)


Map(center=[-3.253, -52.254], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDat…


2.  Obtendo imagem Sentinel-2 com NDVI...
Buscando imagem Sentinel-2 para área de 150km...
Imagem e NDVI calculados!
 Imagem processada com sucesso!

3.  Analisando vegetação na região...

 ANÁLISE DO NDVI NA REGIÃO DE 150KM
 Estatísticas do NDVI:
   • Média: 0.844
   • Desvio padrão: 0.057
   • Status: Muita vegetação (floresta densa)

4.  Criando mapa interativo com layers...

 CRIANDO MAPA INTERATIVO COM LAYERS
 Adicionando layer Google Satellite...
 Adicionando layer Sentinel-2 RGB...
 Adicionando layer NDVI...
 Executando detecção avançada...
 Mapa interativo criado com sucesso!
 Layers disponíveis:
   • Google Satellite (VISÍVEL)
   • Sentinel-2 RGB (OCULTO)
   • NDVI - Vegetação (OCULTO)
   • Áreas de estudo
   • Cidades da região
   • Detecção de áreas claras
   • Detecção avançada

5.  Executando detecção avançada...
 Executando detecção avançada...
 Camada de detecção avançada adicionada!


Map(center=[-3.253, -52.254], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDat…


 MAPA INTERATIVO COMPLETO CRIADO!

 COMO USAR O MAPA:
   • Use o controle no canto superior direito para ligar/desligar layers
   • Sentinel-2 RGB: Visão natural da região
   • NDVI: Mostra vegetação (verde = muita vegetação)
   • Detecção Avançada: Áreas vermelhas = possíveis pistas
   • Zoom: Use scroll do mouse para aproximar

 NDVI médio: 0.844 (alta vegetação)

 ANÁLISE CONCLUÍDA COM SUCESSO!

 DICAS DE INTERPRETAÇÃO:
   • Áreas VERDES no NDVI = Floresta densa
   • Áreas AZUIS/BRANCAS no NDVI = Solo exposto/urbano
   • Áreas VERMELHAS na detecção = Possíveis pistas
   • Compare os layers para melhor análise

 AEROPORTOS NA REGIÃO:
   • Altamira (principal) - coordenadas: [-52.2540, -3.2530]
   • Procure por formas retangulares claras próximas a cidades


In [78]:
# @title MAPA SIMPLES FOCADO NO AEROPORTO
def airport_focus_map():
    """Mapa focado no aeroporto com layers"""
    print("\n MAPA FOCADO NO AEROPORTO DE ALTAMIRA")

    try:
        # Imagem para área menor
        image = get_sentinel2_with_ndvi(roi_10km)

        # Mapa com zoom maior
        Map = geemap.Map(center=[-3.2530, -52.2540], zoom=12)

        # Layer 1: Sentinel-2 RGB
        Map.addLayer(image.clip(roi_10km),
                    {'bands': ['B4', 'B3', 'B2'], 'min': 0, 'max': 3000},
                    'Sentinel-2 RGB (Zoom)', True)

        # Layer 2: NDVI
        Map.addLayer(image.select('NDVI').clip(roi_10km),
                    {'min': -1, 'max': 1, 'palette': ['blue', 'white', 'green']},
                    'NDVI (Zoom)', False)

        # Layer 3: Aeroporto
        airport_point = ee.Geometry.Point(altamira_airport)
        Map.addLayer(airport_point, {'color': 'red', 'pointSize': 20}, 'Aeroporto', True)

        # Layer 4: Detecção
        detection = enhanced_runway_detection(image, roi_10km)
        Map.addLayer(detection,
                    {'palette': ['000000', 'FF0000'], 'opacity': 0.8},
                    'Detecção (Zoom)', False)

        Map.addLayerControl()

        print(" Mapa focado criado!")
        return Map

    except Exception as e:
        print(f" Erro no mapa focado: {e}")
        return None

# Opcional: criar mapa focado
print("\n Criando mapa focado no aeroporto...")
focus_map = airport_focus_map()
if focus_map:
    display(focus_map)
    print(" Análise detalhada da regiao do aeroporto")


 Criando mapa focado no aeroporto...

 MAPA FOCADO NO AEROPORTO DE ALTAMIRA
Buscando imagem Sentinel-2 para área de 150km...
Imagem e NDVI calculados!
 Executando detecção avançada...
 Mapa focado criado!


Map(center=[-3.253, -52.254], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDat…

 Análise detalhada da regiao do aeroporto
